In [8]:
# MATT Code starts here

# Import Dependencies
import pandas as pd
import time
from api_key import api_key

import numpy as np
import requests
import json

# Google API Key
# from config import gkey

In [10]:
# This is the base url for yelp.  Below is the documentation link
# https://www.yelp.com/developers/documentation/v3/business_search

base_url="https://api.yelp.com/v3/businesses/search"

In [11]:
# this line incorporates the api key..I got this line of code from this video:
# https://www.youtube.com/watch?v=GJf7ccRIK4U

my_headers = {"Authorization": "bearer %s" % api_key}

In [14]:
# Now I bring in the IL_Zipcode_CountyName lookup file to get a list of zip codes in Illinois

il_zips_counties = "IL_Zipcode_CountyName.csv"
il_zips_counties_df = pd.read_csv(il_zips_counties)
il_zips_counties_df.head()

ZIP   FIPS CountyName  St                     Name        Lat       Long  \
0  60001  17111    McHenry  IL              60001 Alden  42.421141 -88.616252   
1  60002  17097       Lake  IL            60002 Antioch  42.474263 -88.103323   
2  60004  17031       Cook  IL  60004 Arlington Heights  42.111424 -87.980372   
3  60005  17031       Cook  IL  60005 Arlington Heights  42.064974 -87.982208   
4  60006  17031       Cook  IL  60006 Arlington Heights  42.088133 -87.993611   

   Enc_ZIP  Pops  Area  PopDensity  
0  60033.0     0     0           0  
1      NaN     0     0           0  
2      NaN     0     0           0  
3      NaN     0     0           0  
4  60005.0     0     0           0

In [15]:
# Now create a list of illinois zip codes:
# location_zips = ["61739","60004"," ","61820"]
# location_zips = [" "]

location_zips = il_zips_counties_df["ZIP"].tolist()


In [16]:
# here is the loop that makes callls to the API and forms lists for the information

# Initialize the lists for appending data results:
names = []
zips = []
states=[]
ids=[]
addresses=[]
lats=[]
lngs=[]
zip_counter = 0

# Now loop through the zip codes, using the zip codes for the "location", and searching for the term "fast food"

for loc in location_zips:
    parameters = {"term": "fast food",
              #"radius": 40000,
              "location": loc, 
              "limit": 50,
              #"offset": 51,                       
             }
    time.sleep(1)
    
    # Exception handling.  The outter try/except block is in case the zip code does not exist and the pull is not successful
    #, the inner try/except block is there incase the api returns an incomplete result for a given zip code
    
    try:
        response = requests.get(url = base_url, params = parameters, headers = my_headers)
        business_data = response.json()
        zip_counter += 1
        print(f"Search {zip_counter} for zip code {loc}:")

        for x in range (len(business_data["businesses"])):
        
            try:
                print(f"...........Searching result {x}....")
                names.append(business_data["businesses"][x]["name"])
                zips.append(business_data["businesses"][x]["location"]["zip_code"])
                states.append(business_data["businesses"][x]["location"]["state"])
                ids.append(business_data["businesses"][x]["id"])
                addresses.append(business_data["businesses"][x]["location"]["display_address"])
                lats.append(business_data["businesses"][x]["coordinates"]["latitude"])
                lngs.append(business_data["businesses"][x]["coordinates"]["longitude"])
            except (KeyError, IndexError):
                print("Missing field/result... skipping.")
        
    except (KeyError, IndexError):
        print(f"Zip code {loc} is not found.....skipping:")
        pass       
            
    print(f"the result count so far is {x}")
    
    
    # yelp only returns 50 results per call, and only 5000 calls per day
    # If there are more than 50 results, then you have to put an offset in the paramters.
    # so the next step checks to see if the first call returns 50 results....if not it continues to the next zip code
    # if it does return 50, it does a subsequent call using the offset = 51 to get results 50-100
    
    # PLEASE NOTE:  I did not try to pull more than 100 results per zip code because of the daily call limit issue; 
    # however, each zip code pull brings in results from neighboring zip codes as well, 
    # so I am making an assumption that a search within a dense area of restaurants will also have a dense 
    # number of zip codes, and all the locations will be brought in due to the overlapping  
    
    # PLEASE ALSO NOTE: since each call bring in some results from neighboring zip codes, there is some overlapping
    # in the results.  Therefore the final lists will contain duplicates, which will need to be removed later when
    # we count the number of fast food restaurants.
    
    
    if x < 49:
        continue
        
        
    # Now do a second pull to see if there is more than 50 results (i.e. bring in results 51-100)        
            
    parameters = {"term": "fast food",
              #"radius": 40000,
              "location": loc, 
              "limit": 50,
              "offset": 51,                       
             }
    time.sleep(1)
    
    try:
        response = requests.get(url = base_url, params = parameters, headers = my_headers)
        business_data = response.json()
        print(f"Searching zip code {loc} one more time:")

        for x in range (len(business_data["businesses"])):
        
            try:
                print(f"...........Searching result {x+50}....")
                names.append(business_data["businesses"][x]["name"])
                zips.append(business_data["businesses"][x]["location"]["zip_code"])
                states.append(business_data["businesses"][x]["location"]["state"])
                ids.append(business_data["businesses"][x]["id"])
                addresses.append(business_data["businesses"][x]["location"]["display_address"])
                lats.append(business_data["businesses"][x]["coordinates"]["latitude"])
                lngs.append(business_data["businesses"][x]["coordinates"]["longitude"])
            except (KeyError, IndexError):
                print("Missing field/result... skipping.")
        
    except (KeyError, IndexError):
        print(f"Zip code {loc} is not found.....skipping:")
        pass       
         

Searching zip code 60001:
...........Searching result 0....
...........Searching result 1....
...........Searching result 2....
...........Searching result 3....
...........Searching result 4....
x is 4
Searching zip code 60002:
...........Searching result 0....
...........Searching result 1....
...........Searching result 2....
...........Searching result 3....
...........Searching result 4....
...........Searching result 5....
...........Searching result 6....
...........Searching result 7....
...........Searching result 8....
...........Searching result 9....
...........Searching result 10....
...........Searching result 11....
...........Searching result 12....
...........Searching result 13....
...........Searching result 14....
...........Searching result 15....
...........Searching result 16....
...........Searching result 17....
...........Searching result 18....
...........Searching result 19....
...........Searching result 20....
...........Searching result 21....
...........

Searching zip code 60005 one more time:
...........Searching result 50....
...........Searching result 51....
...........Searching result 52....
...........Searching result 53....
...........Searching result 54....
...........Searching result 55....
...........Searching result 56....
...........Searching result 57....
...........Searching result 58....
...........Searching result 59....
...........Searching result 60....
...........Searching result 61....
...........Searching result 62....
...........Searching result 63....
...........Searching result 64....
...........Searching result 65....
...........Searching result 66....
...........Searching result 67....
...........Searching result 68....
...........Searching result 69....
...........Searching result 70....
...........Searching result 71....
...........Searching result 72....
...........Searching result 73....
...........Searching result 74....
...........Searching result 75....
...........Searching result 76....
...........Sear

Searching zip code 60008 one more time:
...........Searching result 50....
...........Searching result 51....
...........Searching result 52....
...........Searching result 53....
...........Searching result 54....
...........Searching result 55....
...........Searching result 56....
...........Searching result 57....
...........Searching result 58....
...........Searching result 59....
...........Searching result 60....
...........Searching result 61....
...........Searching result 62....
...........Searching result 63....
...........Searching result 64....
...........Searching result 65....
...........Searching result 66....
...........Searching result 67....
...........Searching result 68....
...........Searching result 69....
...........Searching result 70....
...........Searching result 71....
...........Searching result 72....
...........Searching result 73....
...........Searching result 74....
...........Searching result 75....
...........Searching result 76....
...........Sear

Searching zip code 60012:
...........Searching result 0....
...........Searching result 1....
...........Searching result 2....
...........Searching result 3....
...........Searching result 4....
...........Searching result 5....
...........Searching result 6....
...........Searching result 7....
...........Searching result 8....
...........Searching result 9....
...........Searching result 10....
...........Searching result 11....
...........Searching result 12....
...........Searching result 13....
...........Searching result 14....
...........Searching result 15....
...........Searching result 16....
...........Searching result 17....
...........Searching result 18....
...........Searching result 19....
...........Searching result 20....
...........Searching result 21....
...........Searching result 22....
...........Searching result 23....
...........Searching result 24....
...........Searching result 25....
...........Searching result 26....
...........Searching result 27....
....

Searching zip code 60014 one more time:
...........Searching result 50....
...........Searching result 51....
...........Searching result 52....
...........Searching result 53....
...........Searching result 54....
...........Searching result 55....
...........Searching result 56....
...........Searching result 57....
...........Searching result 58....
...........Searching result 59....
...........Searching result 60....
...........Searching result 61....
...........Searching result 62....
...........Searching result 63....
...........Searching result 64....
...........Searching result 65....
...........Searching result 66....
...........Searching result 67....
...........Searching result 68....
...........Searching result 69....
...........Searching result 70....
...........Searching result 71....
...........Searching result 72....
...........Searching result 73....
...........Searching result 74....
...........Searching result 75....
...........Searching result 76....
...........Sear

...

Searching zip code 62972 one more time:
...........Searching result 50....
...........Searching result 51....
...........Searching result 52....
...........Searching result 53....
...........Searching result 54....
...........Searching result 55....
...........Searching result 56....
...........Searching result 57....
...........Searching result 58....
...........Searching result 59....
...........Searching result 60....
...........Searching result 61....
...........Searching result 62....
...........Searching result 63....
...........Searching result 64....
...........Searching result 65....
...........Searching result 66....
...........Searching result 67....
...........Searching result 68....
Searching zip code 62973:
...........Searching result 0....
...........Searching result 1....
...........Searching result 2....
...........Searching result 3....
...........Searching result 4....
...........Searching result 5....
...........Searching result 6....
...........Searching result 7..

Searching zip code 62982:
...........Searching result 0....
...........Searching result 1....
...........Searching result 2....
...........Searching result 3....
...........Searching result 4....
...........Searching result 5....
...........Searching result 6....
...........Searching result 7....
...........Searching result 8....
...........Searching result 9....
...........Searching result 10....
...........Searching result 11....
...........Searching result 12....
...........Searching result 13....
...........Searching result 14....
...........Searching result 15....
...........Searching result 16....
...........Searching result 17....
...........Searching result 18....
...........Searching result 19....
...........Searching result 20....
...........Searching result 21....
...........Searching result 22....
x is 22
Searching zip code 62983:
...........Searching result 0....
...........Searching result 1....
...........Searching result 2....
...........Searching result 3....
.........

Searching zip code 62988 one more time:
...........Searching result 50....
...........Searching result 51....
...........Searching result 52....
...........Searching result 53....
...........Searching result 54....
...........Searching result 55....
...........Searching result 56....
...........Searching result 57....
...........Searching result 58....
...........Searching result 59....
...........Searching result 60....
...........Searching result 61....
...........Searching result 62....
...........Searching result 63....
...........Searching result 64....
...........Searching result 65....
...........Searching result 66....
...........Searching result 67....
Searching zip code 62990:
...........Searching result 0....
...........Searching result 1....
...........Searching result 2....
...........Searching result 3....
...........Searching result 4....
...........Searching result 5....
...........Searching result 6....
...........Searching result 7....
...........Searching result 8...

Searching zip code 62995 one more time:
...........Searching result 50....
...........Searching result 51....
...........Searching result 52....
...........Searching result 53....
...........Searching result 54....
...........Searching result 55....
...........Searching result 56....
...........Searching result 57....
...........Searching result 58....
...........Searching result 59....
...........Searching result 60....
...........Searching result 61....
...........Searching result 62....
...........Searching result 63....
...........Searching result 64....
...........Searching result 65....
...........Searching result 66....
...........Searching result 67....
...........Searching result 68....
...........Searching result 69....
...........Searching result 70....
...........Searching result 71....
...........Searching result 72....
...........Searching result 73....
...........Searching result 74....
...........Searching result 75....
...........Searching result 76....
...........Sear

Searching zip code 62998 one more time:
...........Searching result 50....
...........Searching result 51....
...........Searching result 52....
...........Searching result 53....
...........Searching result 54....
...........Searching result 55....
...........Searching result 56....
...........Searching result 57....
...........Searching result 58....
...........Searching result 59....
...........Searching result 60....
...........Searching result 61....
...........Searching result 62....
...........Searching result 63....
...........Searching result 64....
...........Searching result 65....
...........Searching result 66....
...........Searching result 67....
...........Searching result 68....
...........Searching result 69....
...........Searching result 70....
...........Searching result 71....
...........Searching result 72....
...........Searching result 73....
...........Searching result 74....
...........Searching result 75....
...........Searching result 76....
...........Sear

In [17]:
# create a data frame using the lists made in the API call

yelp_fastfood_dict = {
    "id": ids,
    "name": names,
    "Address": addresses,
    "zip code": zips,
    "state": states,
    "lat": lats,
    "lng": lngs,
}
yelp_fastfood_df = pd.DataFrame(yelp_fastfood_dict)
yelp_fastfood_df

id             name  \
0      O20eGNVmF9FVQd_3t_lcmg        Taco Bell   
1      h0anlZoscW80pfXOjU-pug       McDonald's   
2      veyT9UbcbsgPupFhdDUfEw      Dairy Queen   
3      coQSOoH3npgjUPYvHCZuUA           Subway   
4      Jtyjr-eht4t5OVyZZj5WRA         Culver's   
...                       ...              ...   
98140  6RJCbXKlLuT5TgffREX0Sw        Pizza Hut   
98141  BBzRnMAxeK_VSxsIvWsR_g        Pizza Hut   
98142  4piSmfIuQgKoi6oVM2tvyg  The Pig Bar-B-Q   
98143  1mnOou0dFOw4HXs1NXu1VA      Dairy Queen   
98144  p1IhkYKuBfutC6zGwRaBTA       McDonald's   

                                            Address zip code state        lat  \
0            [325 S Division St, Harvard, IL 60033]    60033    IL  42.414234   
1               [352 S Division, Harvard, IL 60033]    60033    IL  42.409128   
2            [605 S Division St, Harvard, IL 60033]    60033    IL  42.406180   
3            [360 S Division St, Harvard, IL 60033]    60033    IL  42.408491   
4           [1060 S Division St, Harvard, IL 60033]    60033    IL  42.405404   
...                                             ...      ...   ...        ...   
98140  [126-128 E Main St, Fredericktown, MO 63645]    63645    MO  37.559771   
98141          [1801 N Market St, Sparta, IL 62286]    62286    IL  38.147357   
98142         [910 Hwy Oo, Fredericktown, MO 63645]    63645    MO  37.574378   
98143       [106 W Broadway, Steeleville, IL 62288]    62288    IL  38.006812   
98144    [8349 Enterprise Rd, Bloomsdale, MO 63627]    63627    MO  38.005491   

             lng  
0     -88.613502  
1     -88.612985  
2     -88.614069  
3     -88.612911  
4     -88.613068  
...          ...  
98140 -90.293564  
98141 -89.704056  
98142 -90.288830  
98143 -89.658853  
98144 -90.225702  

[98145 rows x 7 columns]

In [18]:
# write the results to a csv
yelp_fastfood_df.to_csv("yelp_fastfood_with_duplicates.csv")

In [19]:
# now do a check to see how many distinct restaurant ID's are in the dataframe
group_by_id = yelp_fastfood_df.groupby( ["id"])
distinct_ids = group_by_id["id"].value_counts()
distinct_ids

id                      id                    
--0OK34lFbyyf4q16yDoGw  --0OK34lFbyyf4q16yDoGw    11
--GvS1gnXSqboHluetk9_Q  --GvS1gnXSqboHluetk9_Q    21
--dIVNPnqmx9l0UipYX6oQ  --dIVNPnqmx9l0UipYX6oQ    36
--fVs_GNeavkOOybb5WNaA  --fVs_GNeavkOOybb5WNaA    13
--kVRdC7JJ2Ph5UaXQw6aA  --kVRdC7JJ2Ph5UaXQw6aA     4
                                                  ..
zwlByG9L7fqFFXr_uyXaXg  zwlByG9L7fqFFXr_uyXaXg    31
zx2Ms-G5pqXI1_A0JVv6gw  zx2Ms-G5pqXI1_A0JVv6gw    16
zxQsRikKcEzfvFz-cD3xsw  zxQsRikKcEzfvFz-cD3xsw     1
zxYsFliXZ1ZGIkm_0fzeoA  zxYsFliXZ1ZGIkm_0fzeoA     1
zyCLNfhtvC-Ki508z17ETg  zyCLNfhtvC-Ki508z17ETg     6
Name: id, Length: 9124, dtype: int64